# Mimic of the DES night summary, but for Rubin Observatory

In [1]:
# This cell is only for setting parameter defaults
day_obs = "2027-11-10"

In [45]:
import datetime
import sys
import pandas as pd
import bokeh
import bokeh.io
import bokeh.plotting
import bokeh.models
import bokeh.transform
import bokeh.layouts
import sqlite3
import numpy as np
import healpy
import astropy
from astropy.time import Time
from lsst.resources import ResourcePath

In [46]:
sys.path.insert(0, '/sdf/data/rubin/user/neilsen/devel/uranography')
sys.path.insert(0, '/sdf/data/rubin/user/neilsen/devel/rubin_scheduler')
sys.path.insert(0, '/sdf/data/rubin/user/neilsen/devel/schedview')

In [47]:
import rubin_scheduler
import rubin_scheduler.utils
import rubin_scheduler.site_models
import schedview.compute.astro
import uranography
from uranography.api import Planisphere

In [48]:
bokeh.io.output_notebook()

Loading BokehJS ...

In [49]:
astropy.utils.iers.conf.iers_degraded_accuracy = 'ignore'

In [6]:
baseline_opsim_rp = ResourcePath('/sdf/group/rubin/web_data/sim-data/sims_featureScheduler_runs3.4/baseline/baseline_v3.4_10yrs.db')
day_obs_mjd = int(Time(day_obs).mjd)

In [7]:
band_cmap = bokeh.transform.factor_cmap(
    'filter',
    ('#56b4e9', '#008060', '#ff4000', '#850000', '#6600cc', '#000000'),
    ['u', 'g', 'r', 'i', 'z', 'y'])

In [8]:
fiducial_depth = {
                "u": 23.71,
                "g": 24.67,
                "r": 24.24,
                "i": 23.82,
                "z": 23.21,
                "y": 22.40,
}

In [9]:
def visit_query(visit_resource_path, query):
    with baseline_opsim_rp.as_local() as local_baseline_opsim_rp:
        with sqlite3.connect(local_baseline_opsim_rp.ospath) as baseline_db_connection:
            visits = pd.read_sql_query(query, baseline_db_connection)

    visits.set_index('observationId', inplace=True)
    
    # Add start time
    start_time = pd.to_datetime(visits['observationStartMJD'] + 2400000.5, origin='julian', unit='D')
    visits.insert(0, 'start_time', start_time)

    # Add day_obs
    day_obs_mjd = np.floor(visits['observationStartMJD'] - 0.5).astype('int')
    day_obs_datetime = Time(day_obs_mjd, format='mjd').datetime
    day_obs_date = [datetime.date(t.year, t.month, t.day) for t in day_obs_datetime]
    day_obs_iso8601 = tuple(str(d) for d in day_obs_date)
    visits.insert(1, 'day_obs_mjd', day_obs_mjd)
    visits.insert(2, 'day_obs_date', day_obs_date)
    visits.insert(3, 'day_obs_iso8601', day_obs_iso8601)

    # Add coordinates tuple
    coord_column = max(tuple(visits.columns).index('fieldRA'), tuple(visits.columns).index('fieldDec')) + 1
    visits.insert(coord_column, 'coords', list(zip(visits['fieldRA'], visits['fieldDec'])))
    
    # Add derived depth columns
    depth_col_index = tuple(visits.columns).index('fiveSigmaDepth')
    tau = 10**(0.8*(visits.fiveSigmaDepth - visits['filter'].map(fiducial_depth)))
    t_eff = visits['visitExposureTime'] * tau
    visits.insert(depth_col_index+1, 'tau', tau)
    visits.insert(depth_col_index+2, 'teff', t_eff)

    # Add time between successive exposures
    # Assume the previous visits ended at its observationStartMJD + visitTime,
    # That this visit ends at its own observationStartMJD + visitTime,
    # and visitExposureTime does not count as overhead.
    overhead = visits['observationStartMJD'].diff()*24*60*60 - visits['visitTime'].shift(1) + visits['visitTime'] - visits['visitExposureTime']
    slew_time_col_index = tuple(visits.columns).index('slewTime')
    visits.insert(slew_time_col_index + 1, 'overhead', overhead)

    #
    filter_col_index = tuple(visits.columns).index('filter')
    previous_filter = visits['filter'].shift(1)
    visits.insert(filter_col_index + 1, 'previous_filter', previous_filter)
    
    return visits

In [10]:
visits = visit_query(
    baseline_opsim_rp,
    f"SELECT * FROM observations WHERE FLOOR(observationStartMJD-0.5)={day_obs_mjd}"
)

Using fiducial depths for t_eff calculation from https://github.com/lsst-sims/smtn-002/blob/main/notebooks/teff_fiducial.ipynb commit e367d65.
These probably should be updated.

In [11]:
visits.head()['start_time']

observationId
579724   2027-11-11 00:11:32.450518784
579725   2027-11-11 00:11:52.802209024
579726   2027-11-11 00:12:13.576668672
579727   2027-11-11 00:12:34.355996928
579728   2027-11-11 00:12:54.676546560
Name: start_time, dtype: datetime64[ns]

In [12]:
visits.head().shift(1)['start_time']

observationId
579724                             NaT
579725   2027-11-11 00:11:32.450518784
579726   2027-11-11 00:11:52.802209024
579727   2027-11-11 00:12:13.576668672
579728   2027-11-11 00:12:34.355996928
Name: start_time, dtype: datetime64[ns]

In [13]:
visits.T

observationId                                          579724  \
start_time                      2027-11-11 00:11:32.450518784   
day_obs_mjd                                             61719   
day_obs_date                                       2027-11-10   
day_obs_iso8601                                    2027-11-10   
fieldRA                                             269.27113   
fieldDec                                           -29.854456   
coords               (269.2711297367811, -29.854455605982313)   
observationStartMJD                              61720.008014   
flush_by_mjd                                     61720.030969   
visitExposureTime                                        15.0   
filter                                                      i   
previous_filter                                          None   
rotSkyPos                                          196.037246   
rotSkyPos_desired                                         0.0   
numExposures                                                1   
airmass                                              2.091462   
seeingFwhm500                                        0.529935   
seeingFwhmEff                                        1.123266   
seeingFwhmGeom                                       0.975325   
skyBrightness                                       17.547504   
night                                                     924   
slewTime                                           109.197521   
overhead                                                  NaN   
visitTime                                                16.0   
slewDistance                                         62.67202   
fiveSigmaDepth                                      21.844306   
tau                                                  0.026269   
teff                                                 0.394036   
altitude                                            28.563633   
azimuth                                            250.203718   
paraAngle                                          110.412566   
cloud                                                     0.0   
moonAlt                                             43.731293   
sunAlt                                             -12.364477   
note                                     twilight_near_sun, 0   
target                                                          
fieldId                                                    -1   
proposalId                                                  8   
block_id                                                    1   
observationStartLST                                342.059104   
rotTelPos                                          -53.550188   
rotTelPos_backup                                          0.0   
moonAz                                              36.647206   
sunAz                                              241.305973   
sunRA                                               225.51604   
sunDec                                             -17.184508   
moonRA                                               7.579039   
moonDec                                              8.624008   
moonDistance                                       101.451909   
solarElong                                          41.793083   
moonPhase                                           78.953684   
cummTelAz                                         -109.796282   
scripted_id                                                 0   

observationId                                          579725  \
start_time                      2027-11-11 00:11:52.802209024   
day_obs_mjd                                             61719   
day_obs_date                                       2027-11-10   
day_obs_iso8601                                    2027-11-10   
fieldRA                                            268.088816   
fieldDec                                           -32.487105   
coords               (268.08881571

## Conditions and statistics

### Sun and Moon

In [52]:
day_obs_datetime = Time(day_obs_mjd, format='mjd').datetime
day_obs_date = datetime.date(day_obs_datetime.year, day_obs_datetime.month, day_obs_datetime.day)
night_events = schedview.compute.astro.night_events(day_obs_date)
night_events

MJD         LST                              UTC  \
event                                                                        
sunset           61719.964397  326.317045 2027-11-10 23:08:43.921000+00:00   
sun_n12_setting  61720.006751  341.606008 2027-11-11 00:09:43.253000+00:00   
sun_n18_setting  61720.029259  349.731385 2027-11-11 00:42:08.019000+00:00   
sun_n18_rising   61720.341286  102.368620 2027-11-11 08:11:27.145000+00:00   
sun_n12_rising   61720.363801  110.495923 2027-11-11 08:43:52.372000+00:00   
sunrise          61720.406151  125.783725 2027-11-11 09:44:51.427000+00:00   
moonrise         61720.879471  296.645438 2027-11-11 21:06:26.274000+00:00   
moonset          61720.318827   94.261087 2027-11-11 07:39:06.650000+00:00   
night_middle     61720.185274   46.050385 2027-11-11 04:26:47.674000+00:00   

                               Chile/Continental  
event                                             
sunset          2027-11-10 20:08:43.921000-03:00  
sun_n12_setting 2027-11-10 21:09:43.253000-03:00  
sun_n18_setting 2027-11-10 21:42:08.019000-03:00  
sun_n18_rising  2027-11-11 05:11:27.145000-03:00  
sun_n12_rising  2027-11-11 05:43:52.372000-03:00  
sunrise         2027-11-11 06:44:51.427000-03:00  
moonrise        2027-11-11 18:06:26.274000-03:00  
moonset         2027-11-11 04:39:06.650000-03:00  
night_middle    2027-11-11 01:26:47.674000-03:00

In [54]:
print(f"Moon phase: {visits['moonPhase'].median()}")

Moon phase: 79.61913341394256


### Numbers of exposures, and gaps between them

In [77]:
relative_start_time = (visits['observationStartMJD'].min() - night_events.loc['sun_n12_setting','MJD'])*60*24
print(f"Open shutter of first exposure: {relative_start_time} minutes before 12 degree evening twilight")

relative_end_time = ((visits['observationStartMJD'] + visits['visitTime']/(24*60*60)).max() - night_events.loc['sun_n12_rising','MJD'])*60*24
print(f"Close shutter time of last exposure: {-1*relative_end_time} minutes after 12 degree morning twilight")

total_time = ((visits['observationStartMJD'] + visits['visitTime']/(24*60*60)).max() - visits['observationStartMJD'].min())*24
print(f"Total wall clock time: {total_time} hours")

num_exposures = len(visits)
print(f"Number of exposures: {num_exposures}")

total_exptime = visits.visitExposureTime.sum()/(60*60)
print(f"Total open shutter time: {total_exptime} hours")

mean_gap_time = 60*60*(total_time - total_exptime)/(num_exposures - 1)
print(f"Mean gap time: {mean_gap_time} seconds")

median_gap_time = visits.overhead.median()
print(f"Median gap time: {median_gap_time} seconds")

Open shutter of first exposure: 1.81995868566446 minutes before 12 degree evening twilight
Close shutter time of last exposure: 0.5028912029229105 minutes after 12 degree morning twilight
Total wall clock time: 8.530485672934446 hours
Number of exposures: 807
Total open shutter time: 6.170833333333333 hours
Mean gap time: 10.539390102436734 seconds
Median gap time: 8.721548987086862 seconds


## Histogram of gaps between exposures

In [14]:
bins = np.arange(0, 30)
hist, edges = np.histogram(visits.overhead, density=False, bins=bins)
p1 = bokeh.plotting.figure(title='Overhead', y_axis_label='Overhead (seconds)')
p1.quad(top=hist, bottom=0, left=edges[:-1], right=edges[1:],
         fill_color="skyblue", line_color="white")

p2 = bokeh.plotting.figure(title='Overhead vs. slew distance', y_axis_label='overhead (sec.)', x_axis_label='slew distance (deg.)')
for band in band_cmap.transform.factors:
    these_visits = visits.query(f'filter == "{band}"')
    if len(these_visits) > 0:
        p2.circle(x='slewDistance', y='overhead', color=band_cmap, fill_alpha=0.3, source=these_visits, legend_label=band)

legend = p2.legend[0]
legend.orientation = 'horizontal'
p2.add_layout(legend, 'below')

gap_plots = bokeh.layouts.row([p1, p2])

bokeh.io.show(gap_plots)

## Long gaps between exposures

In [15]:
num_gaps = 10
long_gap_visits = visits.sort_values('overhead', ascending=False).query('overhead>30').loc[:, ['start_time', 'overhead', 'slewDistance', 'filter', 'previous_filter']].sort_values('observationId')
long_gap_visits

start_time    overhead  slewDistance filter  \
observationId                                                                  
579805        2027-11-11 00:40:22.900316160   75.217132     51.053798      i   
579808        2027-11-11 00:43:04.884913152   31.850945     30.604254      i   
579858        2027-11-11 01:17:11.599138560  124.000000      2.970633      z   
579903        2027-11-11 01:47:07.799655424   65.661567     64.466271      z   
579953        2027-11-11 02:21:26.832824320  124.000000      2.796798      i   
579996        2027-11-11 02:51:08.078885888  124.000000     53.224223      z   
580041        2027-11-11 03:21:00.661760000   60.706758     26.822188      z   
580091        2027-11-11 03:55:46.119931392  124.000000      6.254253      i   
580151        2027-11-11 04:35:35.124394240   46.805341     10.096796      i   
580183        2027-11-11 04:58:21.028633088  124.000000      3.033959      z   
580226        2027-11-11 05:27:16.752752896   53.137966     29.795162      z   
580276        2027-11-11 06:01:36.175740672  124.000000      7.506300      y   
580417        2027-11-11 07:33:41.087233792   51.869968     40.874032      y   
580419        2027-11-11 07:36:07.909651968   77.390940     53.913318      y   
580431        2027-11-11 07:45:07.556815360   57.219982     39.134170      y   
580439        2027-11-11 07:51:03.109865728   46.635791     10.930710      y   
580450        2027-11-11 07:59:38.673595136   78.123716     35.280785      y   
580455        2027-11-11 08:03:47.852006144   58.450409     19.810694      y   
580459        2027-11-11 08:06:51.097723136   32.863462     20.751219      y   
580473        2027-11-11 08:16:52.505283840   53.036928     22.500740      y   
580477        2027-11-11 08:22:03.638659840  157.000000     77.517901      z   
580530        2027-11-11 08:42:48.198958080  144.919178     66.170508      z   

              previous_filter  
observationId                  
579805                      i  
579808                      i  
579858                      i  
579903                      z  
579953                      z  
579996                      i  
580041                      z  
580091                      z  
580151                      i  
580183                      i  
580226                      z  
580276                      z  
580417                      y  
580419                      y  
580431                      y  
580439                      y  
580450                      y  
580455                      y  
580459                      y  
580473                      y  
580477                      y  
580530                      z

## PSF Width

In [16]:
p = bokeh.plotting.figure(title='PSF Width', y_axis_label='seeingFwhmEff')
for band in band_cmap.transform.factors:
    these_visits = visits.query(f'filter == "{band}"')
    if len(these_visits) > 0:
        p.circle(x='start_time', y='seeingFwhmEff', color=band_cmap, fill_alpha=0.3, source=these_visits, legend_label=band)

p.xaxis[0].formatter = bokeh.models.DatetimeTickFormatter(hours="%H:%M")

legend = p.legend[0]
legend.orientation = 'horizontal'
p.add_layout(legend, 'below')
bokeh.io.show(p)

## Instrumental seeing

In [17]:
# Get a seeing model that applies atmospheric and wavelength corrections, but not instrumental contributions.
seeing_model = rubin_scheduler.site_models.SeeingModel(
    telescope_seeing=0.0,
    optical_design_seeing=0.0,
    camera_seeing=0.0
)
seeing_indx_dict = {}
for i, filtername in enumerate(seeing_model.filter_list):
    seeing_indx_dict[filtername] = i
    
noninstrumental_seeing = np.array(tuple(seeing_model(v.seeingFwhm500, v.airmass)['fwhmEff'][seeing_indx_dict[v['filter']]].item() for i, v in visits.iterrows()))
visits['nonatmo_fwhm'] = np.sqrt(visits['seeingFwhmEff']**2 - noninstrumental_seeing**2)

In [18]:
p = bokeh.plotting.figure(title='Instrumental seeing', y_axis_label='Instrumetal contribution to the FWHM')
for band in band_cmap.transform.factors:
    these_visits = visits.query(f'filter == "{band}"')
    if len(these_visits) > 0:
        p.circle(x='start_time', y='nonatmo_fwhm', color=band_cmap, fill_alpha=0.3, source=these_visits, legend_label=band)

p.xaxis[0].formatter = bokeh.models.DatetimeTickFormatter(hours="%H:%M")

legend = p.legend[0]
legend.orientation = 'horizontal'
p.add_layout(legend, 'below')
bokeh.io.show(p)

This perplexes me; I expected the instrumental contribution in simulations to be constant.

## PSF ellipticity

No ellipticity is simulated by opsim.

## Effective exposure time

In [19]:
p = bokeh.plotting.figure(title='Effective exposure time', y_axis_label=r'Effecive exposure time (sec.)')
for band in band_cmap.transform.factors:
    these_visits = visits.query(f'filter == "{band}"')
    if len(these_visits) > 0:
        p.circle(x='start_time', y='teff', color=band_cmap, fill_alpha=0.3, source=these_visits, legend_label=band)

p.xaxis[0].formatter = bokeh.models.DatetimeTickFormatter(hours="%H:%M")

legend = p.legend[0]
legend.orientation = 'horizontal'
p.add_layout(legend, 'below')
bokeh.io.show(p)

## Sky brightness

When run with current opsim simulations, all simulations are either completely spoiled (infinite extinction) or clear (no extinction), and what is recorded is a fraction of the sky covered by clouds.

So, where the DES nightsum plots the extinction, what is plotted here is the recorded fraction cloud cover.

In [20]:
p = bokeh.plotting.figure(title='Sky brightness', y_axis_label=r'cloud cover')
for band in band_cmap.transform.factors:
    these_visits = visits.query(f'filter == "{band}"')
    if len(these_visits) > 0:
        p.circle(x='start_time', y='cloud', color=band_cmap, fill_alpha=0.3, source=these_visits, legend_label=band)

p.xaxis[0].formatter = bokeh.models.DatetimeTickFormatter(hours="%H:%M")

legend = p.legend[0]
legend.orientation = 'horizontal'
p.add_layout(legend, 'below')
bokeh.io.show(p)

## Survey Progress

To do:
1. Separate by band
2. Map completed numbers of exporuses in the background

In [21]:
sky = Planisphere()
sky.plot.circle(
    sky.x_transform("coords"),
    sky.y_transform("coords"),
    source=visits)
sky.decorate()

sky.show(); # If we were in a notebook

## DDF Cadence

In [22]:
time_window_duration = 120
ddf_plot_mjds = np.arange(day_obs_mjd - time_window_duration, day_obs_mjd)

In [23]:
ddf_plot_datetimes = Time(ddf_plot_mjds, format='mjd').datetime
ddf_plot_dates = [datetime.date(t.year, t.month, t.day) for t in ddf_plot_datetimes]
ddf_plot_iso8601 = [str(d) for d in ddf_plot_dates]

In [24]:
ddf_field_names = tuple(rubin_scheduler.utils.ddf_locations().keys())

In [25]:
ddf_visits = visit_query(
    baseline_opsim_rp,
    f"""SELECT * FROM observations
    WHERE target IN {tuple(field_name for field_name in ddf_field_names)}
      AND FLOOR(observationStartMJD-0.5)<={day_obs_mjd}
      AND FLOOR(observationStartMJD-0.5)>{day_obs_mjd-time_window_duration}""")

In [26]:
nightly_ddf = ddf_visits.groupby(['target', 'day_obs_iso8601', 'filter'])['teff'].sum().reset_index()
nightly_ddf = nightly_ddf.pivot(index=['target', 'day_obs_iso8601'], columns='filter', values='teff').fillna(0.0).reset_index().set_index('target')

In [27]:
cadence_plots = []
bands = band_cmap.transform.factors
ddf_field_names = [fn for fn in ddf_field_names if fn in nightly_ddf.index]
x_range = bokeh.models.FactorRange(factors=ddf_plot_iso8601)

for field_name in ddf_field_names:
    last_plot = len(cadence_plots) == len(ddf_field_names)-1

    df = nightly_ddf.loc[field_name, :]
    figure_kwargs = {
        'x_range' : x_range,
        'title': field_name,
        'frame_height': 150,
        'frame_width': 1024,
        'title_location': 'left',
    }

    if not last_plot:
        figure_kwargs['x_axis_location'] = None

    p = bokeh.plotting.figure(**figure_kwargs)

    p.xaxis.major_label_orientation = 'vertical'

    vbar_stack_kwargs = {
        'stackers': bands,
        'x': 'day_obs_iso8601',
        'width': 0.9,
        'source': df,
        'color': band_cmap.transform.palette,
        'fill_alpha': 0.3,
    }
    if last_plot:
        vbar_stack_kwargs['legend_label'] = bands

    p.vbar_stack(**vbar_stack_kwargs)
    if last_plot:
        legend = p.legend[0]
        legend.orientation = 'horizontal'
        p.add_layout(legend, 'below')
    
    cadence_plots.append(p)

cadence_plot_layout = bokeh.layouts.column(cadence_plots)

bokeh.io.show(cadence_plot_layout)

## Table of exposures

In [36]:
displayed_columns = ['start_time', 'fieldRA', 'fieldDec', 'filter', 'visitExposureTime', 'numExposures', 'tau', 'skyBrightness', 'seeingFwhmEff', 'cloud', 'note']
displayed_visits_df = visits.loc[:, displayed_columns]
with pd.option_context('display.max_rows', 2000):
    display(displayed_visits_df)

start_time     fieldRA   fieldDec filter  \
observationId                                                               
579724        2027-11-11 00:11:32.450518784  269.271130 -29.854456      i   
579725        2027-11-11 00:11:52.802209024  268.088816 -32.487105      i   
579726        2027-11-11 00:12:13.576668672  265.681092 -30.138317      i   
579727        2027-11-11 00:12:34.355996928  263.390317 -27.746865      i   
579728        2027-11-11 00:12:54.676546560  264.623586 -25.149016      i   
579729        2027-11-11 00:13:14.994682112  265.785372 -22.539402      i   
579730        2027-11-11 00:13:35.309196800  266.885421 -19.922716      i   
579731        2027-11-11 00:13:56.469009408  272.099047 -14.425671      i   
579732        2027-11-11 00:14:16.780144640  271.147076 -17.041697      i   
579733        2027-11-11 00:14:37.097113344  270.157828 -19.662043      i   
579734        2027-11-11 00:14:57.419191808  269.124280 -22.285370      i   
579735        2027-11-11 00:15:17.745494784  268.038960 -24.908881      i   
579736        2027-11-11 00:15:38.074654464  266.893974 -27.528340      i   
579737        2027-11-11 00:15:58.863839488  269.271130 -29.854456      i   
579738        2027-11-11 00:16:19.210057728  268.088816 -32.487105      i   
579739        2027-11-11 00:16:39.987897344  265.681092 -30.138317      i   
579740        2027-11-11 00:17:00.770242816  263.390317 -27.746865      i   
579741        2027-11-11 00:17:21.086487552  264.623586 -25.149016      i   
579742        2027-11-11 00:17:41.400278016  265.785372 -22.539402      i   
579743        2027-11-11 00:18:01.710366976  266.885421 -19.922716      i   
579744        2027-11-11 00:18:22.838435840  272.099047 -14.425671      i   
579745        2027-11-11 00:18:43.144702720  271.147076 -17.041697      i   
579746        2027-11-11 00:19:03.456642304  270.157828 -19.662043      i   
579747        2027-11-11 00:19:23.773772032  269.124280 -22.285370      i   
579748        2027-11-11 00:19:44.095086080  268.038960 -24.908881      i   
579749        2027-11-11 00:20:04.419377408  266.893974 -27.528340      i   
579750        2027-11-11 00:20:25.211298560  269.271130 -29.854456      i   
579751        2027-11-11 00:20:45.552286464  268.088816 -32.487105      i   
579752        2027-11-11 00:21:06.333465344  265.681092 -30.138317      i   
579753        2027-11-11 00:21:27.118828288  263.390317 -27.746865      i   
579754        2027-11-11 00:21:47.430969088  264.623586 -25.149016      i   
579755        2027-11-11 00:22:07.740575488  265.785372 -22.539402      i   
579756        2027-11-11 00:22:29.334865920  272.476501 -21.929602      i   
579757        2027-11-11 00:22:50.208218624  273.872670 -26.811630      i   
579758        2027-11-11 00:23:10.560673280  272.839389 -29.473676      i   
579759        2027-11-11 00:23:30.914576128  271.759321 -32.134549      i   
579760        2027-11-11 00:23:51.268197376  270.625611 -34.789050      i   
579761        2027-11-11 00:24:12.064141568  266.836375 -35.105963      i   
579762        2027-11-11 00:24:32.865839360  263.016767 -35.305249      i   
579763        2027-11-11 00:24:53.185503744  264.391741 -32.732686      i   
579764        2027-11-11 00:25:13.975413248  268.088816 -32.487105      i   
579765        2027-11-11 00:25:34.310929408  269.271130 -29.854456      i   
579766        2027-11-11 00:25:55.106270208  266.893974 -27.528340      i   
579767        2027-11-11 00:26:15.874091776  270.391667 -27.213913      i   
579768        2027-11-11 00:26:36.204538624  271.457850 -24.570855      i   
579769        2027-11-11 00:26:56.530358784  272.476501 -21.929602      i   
579770        2027-11-11 00:27:17.409304064  273.872670 -26.811630      i   
579771        2027-11-11 00:27:37.755804160  272.839389 -29.473676      i   
579772        2027-11-11 00:27:58.103953664  271.759321 -32.134549      i   
579773        2027-11-11 00:28:18.452062976  270.625611 -34.789050      i   
579774        2027-11-11 00:2

In [32]:
data_source

ColumnDataSource(id='p3067', ...)